## LIME と SHAP によるデータセット分析

In [54]:
import pandas as pd
import python.data_manager as dm
import importlib

In [55]:
importlib.reload(dm)

2024-05-29 10:33:43,030 : python.data_manager : INFO : 32 : Test_message
2024-05-29 10:33:43,030 : INFO : Test_message


<module 'python.data_manager' from '/home/masa1357/Dockerdata/gitfile/Test_LIME_SHAP/src/python/data_manager.py'>

In [56]:
left_df  = dm.read_folder("../data/Reflection/")
right_df = dm.read_folder("../data/Grade/")

2024-05-29 10:33:43,046 : python.data_manager : INFO : 77 : read ../data/Reflection *.csv data...
2024-05-29 10:33:43,046 : INFO : read ../data/Reflection *.csv data...
2024-05-29 10:33:43,050 : python.data_manager : INFO : 80 : read : [PosixPath('../data/Reflection/Course_C-2021-2_Reflection.csv'), PosixPath('../data/Reflection/Course_C-2022-1_Reflection.csv'), PosixPath('../data/Reflection/Course_C-2021-1_Reflection.csv')]
2024-05-29 10:33:43,050 : INFO : read : [PosixPath('../data/Reflection/Course_C-2021-2_Reflection.csv'), PosixPath('../data/Reflection/Course_C-2022-1_Reflection.csv'), PosixPath('../data/Reflection/Course_C-2021-1_Reflection.csv')]
2024-05-29 10:33:43,166 : python.data_manager : INFO : 87 : get 28275 rows.
2024-05-29 10:33:43,166 : INFO : get 28275 rows.
2024-05-29 10:33:43,168 : python.data_manager : INFO : 77 : read ../data/Grade *.csv data...
2024-05-29 10:33:43,168 : INFO : read ../data/Grade *.csv data...
2024-05-29 10:33:43,171 : python.data_manager : INFO :

In [57]:
left_df.head()

userid  course_number  question_number  \
0  C-2021-2_U96              1                1   
1  C-2021-2_U96              1                2   
2  C-2021-2_U96              1                3   
3  C-2021-2_U96              1                4   
4  C-2021-2_U96              1                5   

                    question_content  \
0           今日の内容を自分なりの言葉で説明してみてください   
1        今日の内容で、分かったこと・できたことを書いてください   
2  今日の内容で、分からなかったこと・できなかったことを書いてください   
3                      質問があれば書いてください   
4                今日の授業の感想や反省を書いてください   

                                     answer_content  
0  各種システムの説明。そのあと情報科学とは何かという説明や、これまでの情報の伝え方について学んだ。  
1                   各種システムの使い方の把握。これまでの情報の簡単な歴史の把握。  
2                                          特にありません。  
3                             一度引いたマーカーの消し方がわかりません。  
4     情報科学についておおよそどのようなものなのか理解することができた。これからの授業が楽しみ。

In [58]:
key = "userid"
df = pd.merge(left=left_df, right=right_df, on=key)

In [59]:
df.head()

userid  course_number  question_number  \
0  C-2021-2_U96              1                1   
1  C-2021-2_U96              1                2   
2  C-2021-2_U96              1                3   
3  C-2021-2_U96              1                4   
4  C-2021-2_U96              1                5   

                    question_content  \
0           今日の内容を自分なりの言葉で説明してみてください   
1        今日の内容で、分かったこと・できたことを書いてください   
2  今日の内容で、分からなかったこと・できなかったことを書いてください   
3                      質問があれば書いてください   
4                今日の授業の感想や反省を書いてください   

                                     answer_content grade  
0  各種システムの説明。そのあと情報科学とは何かという説明や、これまでの情報の伝え方について学んだ。     B  
1                   各種システムの使い方の把握。これまでの情報の簡単な歴史の把握。     B  
2                                          特にありません。     B  
3                             一度引いたマーカーの消し方がわかりません。     B  
4     情報科学についておおよそどのようなものなのか理解することができた。これからの授業が楽しみ。     B

In [60]:
LABEL_MAPPING = {"A": 0, "B": 1, "C": 2, "D": 3, "F": 4}
df["label"] = df["grade"].map(LABEL_MAPPING).astype(int)

In [61]:
df, dump = dm.data_clean(df)
dump.head()

2024-05-29 10:33:43,297 : python.data_manager : INFO : 221 : df shape : (28275, 7)
2024-05-29 10:33:43,297 : INFO : df shape : (28275, 7)
2024-05-29 10:33:43,299 : python.data_manager : INFO : 222 : cleaned_df shape : (20291, 7)
2024-05-29 10:33:43,299 : INFO : cleaned_df shape : (20291, 7)
2024-05-29 10:33:43,300 : python.data_manager : INFO : 223 : dumped 7984 rows.
2024-05-29 10:33:43,300 : INFO : dumped 7984 rows.
2024-05-29 10:33:43,310 : python.data_manager : INFO : 231 : dump_df shape : (7984, 7)
2024-05-29 10:33:43,310 : INFO : dump_df shape : (7984, 7)


userid  course_number  question_number  \
7    C-2021-2_U21              1                3   
8    C-2021-2_U21              1                4   
38   C-2021-2_U32              1                4   
43   C-2021-2_U35              1                4   
53  C-2021-2_U121              1                4   

                     question_content answer_content grade  label  
7   今日の内容で、分からなかったこと・できなかったことを書いてください            NaN     C      2  
8                       質問があれば書いてください            NaN     C      2  
38                      質問があれば書いてください            NaN     B      1  
43                      質問があれば書いてください            NaN     B      1  
53                      質問があれば書いてください            NaN     C      2

In [62]:
train, valid, test = dm.sprit_data_for_user(df, key=key, text="answer_content", label="grade", split_rate=[0.8, 0.1, 0.1])

In [63]:
print(f"""
      columns =
      train : {train.columns}
      valid : {valid.columns}
      test  : {test.columns}
      """
)


      columns =
      train : Index(['userid', 'grade', 'text', 'course_number', 'question_number', 'label'], dtype='object')
      valid : Index(['userid', 'grade', 'text', 'course_number', 'question_number', 'label'], dtype='object')
      test  : Index(['userid', 'grade', 'text', 'course_number', 'question_number', 'label'], dtype='object')
      


In [64]:
print(f"""
      rows =
      train : {len(train)}\t- {len(train) / (len(train) + len(valid) + len(test))} %
      valid : {len(valid)}\t- {len(valid) / (len(train) + len(valid) + len(test))} %
      test  : {len(test)}\t- {len(test ) / (len(train) + len(valid) + len(test))} %
      """
)


      rows =
      train : 16142	- 0.7955251096545266 %
      valid : 2097	- 0.10334631117244099 %
      test  : 2052	- 0.10112857917303238 %
      


In [65]:
train.head()

userid grade                                               text  \
0   C-2022-1_U72     C                  情報科学の時間で学習する内容や授業で使う教材システム評価方法の説明   
1   C-2021-1_U70     D                               授業の説明情報伝達の歴史を大まかに学んだ   
2  C-2021-2_U103     B  情報教育が軽視されているが今の世の中で情報について知ることは必須である情報は伝送しやすい形に...   
3  C-2021-2_U139     B  情報科学の発展は目覚ましくインタネットを使うことで様々な情報を２進数に変化し扱うことができる...   
4    C-2022-1_U7     C                                情報科学についてを知ることができました   

  course_number question_number  label  
0            01               1      2  
1            01               1      3  
2            01               1      1  
3            01               1      1  
4            01               1      2

In [66]:
text = "answer_content"
label = "label"
categories = sorted(train["grade"].unique().tolist())
categories

['A', 'B', 'C', 'D', 'F']

In [67]:
# dfの型を確認
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 20291 entries, 0 to 28269
Data columns (total 8 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   userid            20291 non-null  object
 1   course_number     20291 non-null  int64 
 2   question_number   20291 non-null  int64 
 3   question_content  20291 non-null  object
 4   answer_content    20291 non-null  object
 5   grade             20291 non-null  object
 6   label             20291 non-null  int64 
 7   new_column        20291 non-null  object
dtypes: int64(3), object(5)
memory usage: 1.4+ MB


### 分類機実装

In [68]:
import MeCab
import re

tagger = MeCab.Tagger("-Owakati")


def make_wakati(sentence):
    sentence = tagger.parse(sentence)
    sentence = re.sub(r"[0-9０-９a-zA-Zａ-ｚＡ-Ｚ]+", " ", sentence)
    sentence = re.sub(
        r"[\．_－―─！＠＃＄％＾＆\-‐|\\＊\“（）＿■×+α※÷⇒—●★☆〇◎◆▼◇△□(：〜～＋=＝)／*&^%$#@!~`){}［］…\[\]\"\'\”\’:;<>?＜＞〔〕〈〉？、。・,\./『』【】「」→←○《》≪≫\n\u3000]+",
        "",
        sentence,
    )
    wakati = sentence.split(" ")
    wakati = list(filter(("").__ne__, wakati))
    return wakati

In [69]:
from gensim.models import Word2Vec
import numpy as np
import logging
from tqdm import tqdm


# word2vec parameters
num_features = 200
min_word_count = 5
num_workers = 40
context = 10
downsampling = 1e-3
model_name = "word2vec_testcase.model"

# コーパス読み込み
corpus = []
for doc in tqdm(df["answer_content"]):
    corpus.append(make_wakati(doc))


# word2vecモデルの作成＆モデルの保存
print("cleating word2vec model ...")
logging.basicConfig(
    format="%(asctime)s : %(levelname)s : %(message)s", level=logging.INFO
)
model = Word2Vec(
    corpus,
    workers=num_workers,
    hs=0,
    sg=1,
    negative=10,
    epochs=25,
    vector_size=num_features,
    min_count=min_word_count,
    window=context,
    sample=downsampling,
    seed=1,
)
model.save(model_name)
print("Done.")

# word2vecモデルの読み込み
# model = Word2Vec.load(model_name)

# test
# print(model.wv.most_similar("フーリエ"))

100%|██████████| 20291/20291 [00:01<00:00, 15951.18it/s]
2024-05-29 10:33:45,342 : INFO : collecting all words and their counts
2024-05-29 10:33:45,342 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2024-05-29 10:33:45,407 : INFO : PROGRESS: at sentence #10000, processed 410419 words, keeping 6216 word types
2024-05-29 10:33:45,466 : INFO : PROGRESS: at sentence #20000, processed 811430 words, keeping 8380 word types
2024-05-29 10:33:45,468 : INFO : collected 8419 word types from a corpus of 817205 raw words and 20291 sentences
2024-05-29 10:33:45,469 : INFO : Creating a fresh vocabulary
2024-05-29 10:33:45,481 : INFO : Word2Vec lifecycle event {'msg': 'effective_min_count=5 retains 3532 unique words (41.95% of original 8419, drops 4887)', 'datetime': '2024-05-29T10:33:45.481594', 'gensim': '4.3.2', 'python': '3.10.12 (main, Nov 20 2023, 15:14:05) [GCC 11.4.0]', 'platform': 'Linux-6.2.0-34-generic-x86_64-with-glibc2.35', 'event': 'prepare_vocab'}
2024-05-29 

cleating word2vec model ...


2024-05-29 10:33:46,613 : INFO : EPOCH 0 - PROGRESS: at 50.93% examples, 250980 words/s, in_qsize 39, out_qsize 2
2024-05-29 10:33:46,991 : INFO : EPOCH 0: training on 817205 raw words (513132 effective words) took 1.4s, 354614 effective words/s
2024-05-29 10:33:48,019 : INFO : EPOCH 1 - PROGRESS: at 42.89% examples, 228080 words/s, in_qsize 46, out_qsize 0
2024-05-29 10:33:48,443 : INFO : EPOCH 1: training on 817205 raw words (512922 effective words) took 1.4s, 357345 effective words/s
2024-05-29 10:33:49,469 : INFO : EPOCH 2 - PROGRESS: at 39.67% examples, 198475 words/s, in_qsize 51, out_qsize 0
2024-05-29 10:33:49,934 : INFO : EPOCH 2: training on 817205 raw words (513366 effective words) took 1.5s, 349136 effective words/s
2024-05-29 10:33:50,980 : INFO : EPOCH 3 - PROGRESS: at 44.19% examples, 224832 words/s, in_qsize 45, out_qsize 1
2024-05-29 10:33:51,390 : INFO : EPOCH 3: training on 817205 raw words (513209 effective words) took 1.4s, 356771 effective words/s
2024-05-29 10:33

Done.


In [70]:
model.wv.vectors.shape

(3532, 200)

In [72]:
model.wv.most_similar("システム")

[('支援', 0.4690426290035248),
 ('リアル', 0.45977291464805603),
 ('ドル', 0.4541085958480835),
 ('ダッシュボド', 0.44435515999794006),
 ('青色', 0.4361817538738251),
 ('ガイダンス', 0.4349101781845093),
 ('戸惑い', 0.4267682433128357),
 ('監視', 0.4261120855808258),
 ('モニタリング', 0.4178283214569092),
 ('裏側', 0.4103674292564392)]

In [73]:
wakati = [
    "期末",
    "試験",
    "が",
    "終わり",
    "情報",
    "科学",
    "の",
    "履修",
    "を",
    "完了",
    "でき",
    "た",
]
for word in wakati:
    if word in model.wv:
        print(f"{word} はモデルに存在します。")
    else:
        print(f"{word} はモデルに存在しません。")

期末 はモデルに存在します。
試験 はモデルに存在します。
が はモデルに存在します。
終わり はモデルに存在します。
情報 はモデルに存在します。
科学 はモデルに存在します。
の はモデルに存在します。
履修 はモデルに存在します。
を はモデルに存在します。
完了 はモデルに存在します。
でき はモデルに存在します。
た はモデルに存在します。


In [74]:
def wordvec2docvec(sentence):
    # 文章ベクトルの初期値（0ベクトルを初期値とする）
    docvecs = np.zeros(num_features, dtype="float32")

    # 文章に現れる単語のうち、モデルに存在しない単語をカウントする
    denomenator = len(sentence)

    # 文章内の各単語ベクトルを足し合わせる
    for word in sentence:
        try:
            temp = model.wv[word]
            # docvecs += temp
        except:
            denomenator -= 1
            print(f"{word}はモデルに存在しません。")
            continue
        docvecs += temp

    # 文章に現れる単語のうち、モデルに存在した単語の数で割る
    if denomenator > 0:
        docvecs = docvecs / denomenator

    return docvecs

In [75]:
from sklearn.model_selection import train_test_split

print(len(df[text]))
X, Y = [], []
for doc, category in tqdm(zip(df[text], df["grade"])):
    wakati = make_wakati(doc)
    docvec = wordvec2docvec(wakati)
    X.append(list(docvec))
    Y.append(LABEL_MAPPING[category])
data_X = pd.DataFrame(X, columns=["X" + str(i + 1) for i in range(num_features)])
data_Y = pd.DataFrame(Y, columns=["category_id"])

train_x, test_x, train_y, test_y = train_test_split(data_X, data_Y, train_size=0.7)

20291


0it [00:00, ?it/s]

見失うはモデルに存在しません。
素晴らしはモデルに存在しません。
おっちょこちょいはモデルに存在しません。
落とさはモデルに存在しません。
従来はモデルに存在しません。
年代はモデルに存在しません。
工業はモデルに存在しません。
姿はモデルに存在しません。
指摘はモデルに存在しません。
学ぼうはモデルに存在しません。
ビジョンはモデルに存在しません。
問い合わせはモデルに存在しません。
頼もしいはモデルに存在しません。
九州はモデルに存在しません。
見通しはモデルに存在しません。
持てるはモデルに存在しません。
押すはモデルに存在しません。
ふわふわはモデルに存在しません。
なくなりはモデルに存在しません。
ギリシャはモデルに存在しません。
腕はモデルに存在しません。
果たしてはモデルに存在しません。
望遠はモデルに存在しません。
鏡はモデルに存在しません。
主だっはモデルに存在しません。
トンはモデルに存在しません。
届けはモデルに存在しません。
長年はモデルに存在しません。
黄色はモデルに存在しません。
たどっはモデルに存在しません。
及ぼしはモデルに存在しません。
チャイムはモデルに存在しません。
切り替えはモデルに存在しません。
急いはモデルに存在しません。
見返すはモデルに存在しません。
ジェスはモデルに存在しません。
近現代はモデルに存在しません。
点滅はモデルに存在しません。
カナはモデルに存在しません。
受け取れるはモデルに存在しません。
望遠はモデルに存在しません。
鏡はモデルに存在しません。
キロはモデルに存在しません。
メトルはモデルに存在しません。
疎通はモデルに存在しません。
覚えれはモデルに存在しません。
みなおしはモデルに存在しません。
インフラはモデルに存在しません。
たいまつはモデルに存在しません。
電磁はモデルに存在しません。
石はモデルに存在しません。
電源はモデルに存在しません。
原型はモデルに存在しません。
れっきはモデルに存在しません。
大勢はモデルに存在しません。
動向はモデルに存在しません。
探るはモデルに存在しません。
生まれ育っはモデルに存在しません。
もたらしはモデルに存在しません。
類はモデルに存在しません。
大好きはモデルに存在しません。
既視はモデルに存在しません。
去年はモデルに存在しません。
手短はモデ

1364it [00:00, 6808.27it/s]

振り絞っはモデルに存在しません。
バイトキロバイトメガバイトはモデルに存在しません。
メガはモデルに存在しません。
あたりまえはモデルに存在しません。
あたりまえはモデルに存在しません。
ないがしろはモデルに存在しません。
仕切れはモデルに存在しません。
カタカナはモデルに存在しません。
バケツリレはモデルに存在しません。
電磁はモデルに存在しません。
石はモデルに存在しません。
追い求めはモデルに存在しません。
軽量はモデルに存在しません。
危機はモデルに存在しません。
とらわれはモデルに存在しません。
驚かさはモデルに存在しません。
揺るがはモデルに存在しません。
古今はモデルに存在しません。
東西はモデルに存在しません。
各国はモデルに存在しません。
せっかくはモデルに存在しません。
試さはモデルに存在しません。
中継はモデルに存在しません。
こなせれはモデルに存在しません。
飛脚はモデルに存在しません。
早馬はモデルに存在しません。
揚はモデルに存在しません。
キチンとはモデルに存在しません。
出入りはモデルに存在しません。
リアルモリタニングはモデルに存在しません。
べつはモデルに存在しません。
書き換えるはモデルに存在しません。
ありがたくはモデルに存在しません。
妨害はモデルに存在しません。
益々はモデルに存在しません。
そはモデルに存在しません。
戻さはモデルに存在しません。
運ぶはモデルに存在しません。
無謀はモデルに存在しません。
弱はモデルに存在しません。
電波はモデルに存在しません。
無くはモデルに存在しません。
数的はモデルに存在しません。
分間はモデルに存在しません。
整えはモデルに存在しません。
並べれはモデルに存在しません。
イズはモデルに存在しません。
不等はモデルに存在しません。
かぶりはモデルに存在しません。
四苦はモデルに存在しません。
八苦はモデルに存在しません。
度々はモデルに存在しません。
解こうはモデルに存在しません。
映しはモデルに存在しません。
迷子はモデルに存在しません。
済んはモデルに存在しません。
導きはモデルに存在しません。
エントロピエントロピはモデルに存在しません。
約はモデルに存在しません。
掃き溜めはモデルに存在しません。
掃き溜めはモデルに存在しません。
仕切りはモデルに存在しません。
役目はモデ

...

見ようはモデルに存在しません。
中高はモデルに存在しません。
一括りはモデルに存在しません。
上位はモデルに存在しません。
互換はモデルに存在しません。
予備はモデルに存在しません。
校はモデルに存在しません。
べはモデルに存在しません。
値段はモデルに存在しません。
階級はモデルに存在しません。
生みはモデルに存在しません。
色色はモデルに存在しません。
ヒトマップはモデルに存在しません。
ならっはモデルに存在しません。
併用はモデルに存在しません。
占めるはモデルに存在しません。
描けはモデルに存在しません。
ぶぶんはモデルに存在しません。
かっこはモデルに存在しません。
奥行きはモデルに存在しません。
図式はモデルに存在しません。
落とし込みはモデルに存在しません。
受け取らはモデルに存在しません。
戻るはモデルに存在しません。
受けとっはモデルに存在しません。
おかしいはモデルに存在しません。
おぼろはモデルに存在しません。
げはモデルに存在しません。
デはモデルに存在しません。
タグはモデルに存在しません。
ラフはモデルに存在しません。
安易はモデルに存在しません。
どきはモデルに存在しません。
招きはモデルに存在しません。
延ばすはモデルに存在しません。
くださるはモデルに存在しません。
逆手はモデルに存在しません。
招けるはモデルに存在しません。
たけれはモデルに存在しません。
パイチャトデタはモデルに存在しません。
引き起こすはモデルに存在しません。
進まはモデルに存在しません。
促すはモデルに存在しません。
度々はモデルに存在しません。
マスコミはモデルに存在しません。
むしろはモデルに存在しません。
悪化はモデルに存在しません。
使い分けれるはモデルに存在しません。
低はモデルに存在しません。
投影はモデルに存在しません。
貴重はモデルに存在しません。
うけはモデルに存在しません。
本番はモデルに存在しません。
割り切るはモデルに存在しません。
肝要はモデルに存在しません。
縦線はモデルに存在しません。
横線はモデルに存在しません。
フィルムはモデルに存在しません。
そこそこはモデルに存在しません。
絞れるはモデルに存在しません。
細やかはモデルに存在しません。
悩んはモデルに存在しません。
しめすはモデルに存在しません。
ンはモデルに存在しませ

20261it [00:03, 6799.52it/s]

しれるはモデルに存在しません。
映っはモデルに存在しません。
エッヂはモデルに存在しません。
通知はモデルに存在しません。
有機はモデルに存在しません。
低けれはモデルに存在しません。
手応えはモデルに存在しません。
間に合わはモデルに存在しません。
即答はモデルに存在しません。
頑張らはモデルに存在しません。
急いはモデルに存在しません。
筆記はモデルに存在しません。
筆記はモデルに存在しません。
むずかしいはモデルに存在しません。
筆記はモデルに存在しません。
かんじはモデルに存在しません。
気付きはモデルに存在しません。
かんじはモデルに存在しません。
ぼかしはモデルに存在しません。
うめるはモデルに存在しません。
必死はモデルに存在しません。
といはモデルに存在しません。
総まとめはモデルに存在しません。
長かっはモデルに存在しません。
甲斐はモデルに存在しません。
そこそこはモデルに存在しません。
手応えはモデルに存在しません。
朝はモデルに存在しません。
感謝はモデルに存在しません。
甘いはモデルに存在しません。
孤独はモデルに存在しません。
戦いはモデルに存在しません。
昨日はモデルに存在しません。
勘はモデルに存在しません。
黒くはモデルに存在しません。
ドキュメントはモデルに存在しません。
表面はモデルに存在しません。
実力はモデルに存在しません。
埋めれはモデルに存在しません。
さんざんはモデルに存在しません。
激しくはモデルに存在しません。
憤りはモデルに存在しません。
夏休みはモデルに存在しません。
過ごさはモデルに存在しません。
吹っ飛びはモデルに存在しません。
痛いはモデルに存在しません。
狭はモデルに存在しません。
自省はモデルに存在しません。
ズはモデルに存在しません。
モザイクはモデルに存在しません。
ぼかしはモデルに存在しません。
末はモデルに存在しません。
行なわはモデルに存在しません。
いらはモデルに存在しません。
😀はモデルに存在しません。
読み取っはモデルに存在しません。
設問はモデルに存在しません。
設問はモデルに存在しません。
すらすらはモデルに存在しません。
届いはモデルに存在しません。
望めはモデルに存在しません。
クッキリはモデルに存在しません。
けばはモデルに存在しません。
気がかりはモデルに存在しません。
心

20291it [00:03, 5870.67it/s]

タイピングはモデルに存在しません。
空欄はモデルに存在しません。
振り返っはモデルに存在しません。
実力はモデルに存在しません。
サクサクはモデルに存在しません。
縦横はモデルに存在しません。
両はモデルに存在しません。
明度はモデルに存在しません。
たどり着けはモデルに存在しません。
貴重はモデルに存在しません。


In [76]:
data_X.head()

X1        X2        X3        X4        X5        X6        X7  \
0  0.012973 -0.034600 -0.154214  0.011718  0.059926 -0.152761 -0.230280   
1  0.023124 -0.090666 -0.204214 -0.035880  0.034738 -0.096949 -0.275701   
2  0.079451 -0.042952 -0.186534  0.344539 -0.092632 -0.425807 -0.491977   
3  0.036305 -0.057795 -0.067677  0.196915  0.009877 -0.211752 -0.190548   
4 -0.013433 -0.035793 -0.115926 -0.016348  0.004053 -0.089790 -0.257423   

         X8        X9       X10  ...      X191      X192      X193      X194  \
0  0.053029  0.185985  0.104208  ...  0.026758  0.040682 -0.046936 -0.085196   
1  0.106431  0.152739  0.018928  ...  0.026445  0.003619 -0.129655 -0.020331   
2  0.129154  0.039175  0.210147  ... -0.093642 -0.249829 -0.109421 -0.004663   
3  0.068319  0.000314  0.238655  ...  0.061693 -0.095781 -0.086512 -0.177968   
4  0.048121  0.124635  0.064947  ... -0.066361  0.048421 -0.132951 -0.046084   

       X195      X196      X197      X198      X199      X200  
0 -0.101928  0.116551 -0.037350  0.112883  0.057393 -0.161326  
1 -0.084755  0.182466 -0.031769  0.189521  0.012216 -0.205092  
2 -0.086186 -0.027521  0.033631 -0.211655  0.461068 -0.314134  
3 -0.096824  0.155913 -0.107873 -0.001136  0.166046 -0.215973  
4 -0.113483  0.169669 -0.061269  0.077326 -0.015517 -0.152489  

[5 rows x 200 columns]

In [77]:
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
import plotly.express as px

In [78]:
# PCAのインスタンスを作成し、2次元に削減する設定
pca = PCA(n_components=2)
X_pca = pca.fit_transform(data_X)

# PCAの結果をDataFrameに変換
pca_df = pd.DataFrame(X_pca, columns=["Principal Component 1", "Principal Component 2"])
pca_df["Category"] = data_Y["category_id"].values  # カテゴリーラベルを追加

In [79]:
fig = px.scatter(
    pca_df,
    x="Principal Component 1",
    y="Principal Component 2",
    color=pca_df["Category"].astype(str),
    labels={"color": "Category"},
    title="PCA Visualization of Document Vectors",
    width=800,
    height=800,
)
fig.update_traces(
    marker=dict(size=5, opacity=0.8, line=dict(width=0.5, color="DarkSlateGrey"))
)
fig.show()

In [80]:
# t-SNEのパラメータ設定
tsne = TSNE(n_components=2, random_state=42)  # 2次元に削減
X_tsne = tsne.fit_transform(data_X)

# t-SNEの結果をDataFrameに変換
tsne_df = pd.DataFrame(X_tsne, columns=["Dim1", "Dim2"])
tsne_df["Category"] = data_Y["category_id"].values  # カテゴリーラベルを追加

In [81]:
fig = px.scatter(
    tsne_df,
    x="Dim1",
    y="Dim2",
    color=tsne_df["Category"].astype(str),
    labels={"color": "Category"},
    title="t-SNE Visualization of Document Vectors",
    width=800,
    height=800,
)
fig.update_traces(
    marker=dict(size=5, opacity=0.8, line=dict(width=0.5, color="DarkSlateGrey"))
)
fig.show()

In [82]:
import xgboost as xgb
from sklearn.metrics import classification_report

print("Fitting XGboost model ...")
xgb_model = xgb.XGBClassifier()
xgb_model.fit(train_x, train_y)
print("Done.")

# 予測
pred = xgb_model.predict(test_x)
print(classification_report(pred, test_y["category_id"], target_names=categories))

Fitting XGboost model ...
Done.
              precision    recall  f1-score   support

           A       0.02      0.26      0.04        66
           B       0.88      0.57      0.69      5092
           C       0.22      0.39      0.28       914
           D       0.04      0.58      0.07        12
           F       0.01      0.50      0.02         4

    accuracy                           0.54      6088
   macro avg       0.23      0.46      0.22      6088
weighted avg       0.77      0.54      0.62      6088



In [83]:
import lightgbm as lgbm

print("Fitting LightGBM model ...")
lgbm_model = lgbm.LGBMClassifier()
lgbm_model.fit(train_x, train_y)
print("Done.")

# 予測
pred = lgbm_model.predict(test_x)
print(classification_report(pred, test_y["category_id"], target_names=categories))

Fitting LightGBM model ...
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.004568 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 50989
[LightGBM] [Info] Number of data points in the train set: 14203, number of used features: 200
[LightGBM] [Info] Start training from score -2.067335
[LightGBM] [Info] Start training from score -0.622152
[LightGBM] [Info] Start training from score -1.296588
[LightGBM] [Info] Start training from score -3.144476
[LightGBM] [Info] Start training from score -3.905217


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:97: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:132: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().



Done.
              precision    recall  f1-score   support

           A       0.01      0.27      0.02        33
           B       0.91      0.57      0.70      5336
           C       0.18      0.42      0.25       701
           D       0.04      0.50      0.07        14
           F       0.01      0.50      0.02         4

    accuracy                           0.55      6088
   macro avg       0.23      0.45      0.21      6088
weighted avg       0.82      0.55      0.64      6088



In [84]:
from sklearn.ensemble import RandomForestClassifier

rfc = RandomForestClassifier()
rfc.fit(train_x, train_y)
pred = rfc.predict(test_x)
print(classification_report(pred, test_y["category_id"], target_names=categories))


/usr/local/lib/python3.10/dist-packages/sklearn/base.py:1473: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().



              precision    recall  f1-score   support

           A       0.01      0.38      0.02        21
           B       0.92      0.56      0.69      5444
           C       0.15      0.39      0.21       612
           D       0.03      0.67      0.06         9
           F       0.01      1.00      0.02         2

    accuracy                           0.54      6088
   macro avg       0.22      0.60      0.20      6088
weighted avg       0.83      0.54      0.64      6088



In [85]:
from sklearn.feature_extraction.text import TfidfVectorizer

corpus = df[text]
tfidf_vectorizer = TfidfVectorizer(analyzer=make_wakati)
tfidfs = tfidf_vectorizer.fit_transform(corpus)
print(tfidfs.shape)
# (7376, 79673)

tfidf_data_X = pd.DataFrame(
    tfidfs.toarray(), columns=["X" + str(i) for i in range(tfidfs.shape[1])]
)
train_x, test_x, train_y, test_y = train_test_split(data_X, data_Y, train_size=0.7)
lgbm_model = lgbm.LGBMClassifier()
lgbm_model.fit(train_x, train_y)
pred = lgbm_model.predict(test_x)
print(classification_report(pred, test_y["category_id"], target_names=categories))

(20291, 8419)


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:97: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:132: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().



[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.007466 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 50984
[LightGBM] [Info] Number of data points in the train set: 14203, number of used features: 200
[LightGBM] [Info] Start training from score -2.084736
[LightGBM] [Info] Start training from score -0.616397
[LightGBM] [Info] Start training from score -1.298392
[LightGBM] [Info] Start training from score -3.247660
[LightGBM] [Info] Start training from score -3.732263
              precision    recall  f1-score   support

           A       0.02      0.40      0.03        30
           B       0.91      0.56      0.69      5371
           C       0.17      0.41      0.24       671
           D       0.03      0.62      0.06        13
           F       0.00      0.00      0.00         3

    accuracy                           0.54      6088
   macro avg       0.22      0.40      0.20      6088
weigh